In [ ]:
!pip install 

In [4]:
import json
import pandas as pd
import re
import os
import glob

from fuzzywuzzy import fuzz
from fuzzywuzzy import process
from difflib import SequenceMatcher
from rapidfuzz import fuzz, process
import Levenshtein
import numpy as np
import openpyxl as xl
import warnings
from openpyxl import load_workbook

# Settings the warnings to be ignored 
warnings.filterwarnings('ignore') 

In [5]:
commodity='ignite'
jsondir = r'D:\Dev_Playground\10_march\processed_outputs'

In [21]:
def param_matching(masterdf, reportdf):

    report = reportdf
    master = masterdf      
    #lower with remove new line
    report['Param_with_unit'] = report['Param_with_unit'].str.lower().str.replace('\n','', regex=False)

    #Find exact match from master
    df_m = pd.merge(report,master,on='Param_with_unit', how='left')

    #Extract extract match
    df_direct_mapped = df_m.dropna(subset=['Master'])
    df_direct_mapped.reset_index(inplace=True,drop=True)
    print('Report parameters:', report.shape)
    print('Matched by Direct mapping: ', df_direct_mapped.shape)

    if(report.shape[0] > df_direct_mapped.shape[0]):
        print('Fuzzy required')
        #Extract which are exactly not matching
        df_direct_mapped_NA = pd.DataFrame()
        df_direct_mapped_NA = df_m[df_m['Master'].isna()]
        df_direct_mapped_NA.reset_index(inplace=True, drop=True)
        print( 'Need to match with fuzzy:',df_direct_mapped_NA.shape)

        #Find match with fuzzy 
        master_params = list(master['Param_with_unit'])

        # print(df_direct_mapped_NA.shape)
        for i,j in enumerate(df_direct_mapped_NA['Param_with_unit']):
            # print(i)
            # print(j)
            best_match = process.extractOne(j.lower(),master_params)
            # print(best_match)
            df_direct_mapped_NA.loc[i,'param_with_unit_alias'] = best_match[0]
            # print( master.iloc[best_match[2],1])
            df_direct_mapped_NA.loc[i,'master_param'] = master.loc[best_match[2],'Master']
            df_direct_mapped_NA.loc[i,'matching_score'] = round(float(best_match[1]),2)

        #Review and Suggest based on Fuzzy score >92%
        df_direct_mapped_NA['review-suggest'] = np.where(df_direct_mapped_NA['matching_score'] > 92, "matched", "mismatched")

        df_final = pd.concat([df_direct_mapped_NA, df_direct_mapped], ignore_index=True)

        #Columns for checking
        # df_final = df_final[['S.No.','Quality Characteristics','Param_with_unit','Master','param_with_unit_alias','master_param','matching_score','review-suggest']]
    
    else:
        print('All match found')
        df_final = df_direct_mapped
        #Columns for checking
        # df_final = df_final[['S.No.','Quality Characteristics','Param_with_unit','Master']]
        
    return df_final



In [9]:
unit_list = [
    r'% by weight',r'% by wt\.',
    r'mcg/kg', r'(mg/kg)', r'mg/kg',r'mg/Kg',r'cfu per g',r"CFU/ml", r'cfu/ml',r'cfu/g',r'Cfu/g',r'(v/w)',r"%V/W", r"%w/w",r'%', r'µg/kg', r'CFU/g',r'g/100ml',r'gm/L',r'g/L',r'g/100g',r'g/Kg',r'm/kg', r'Per 25g',
    r'/25 g', r'g/kg',  r'/25g', r'Âµg/kg', r'mL/100g',r'ml/100g', r' mm$',
    r'ug/kg', r'μg/kg',r'µg/Kg',r'g/lit', r'g/l',r'g/L' 
]


pattern = r'\s*(' + '|'.join(unit_list) + r')\s*'
# pattern = 

# unit_list = pattern

# Function to extract unit
def extract_unit(row):
    for col in ['Quality Characteristics', 'Results', 'Units']:
        if pd.notna(row[col]):
            match = re.search(pattern, str(row[col]), re.IGNORECASE)
            # print(match)
            if match:
                return match.group(1)
    return None
def unit_cleaning(df_data):
    df = df_data.copy()
    # Apply function to extract unit
    df['Unit_extracted'] = df.apply(extract_unit, axis=1)

    # Clean Results column by removing units
    def clean_results(row):
        if pd.notna(row['Results']):
            return re.sub(pattern, '', row['Results']).strip()
        return row['Results']
    
     # Clean Results column by removing units
    def clean_param(row):
        if pd.notna(row['Quality Characteristics']):
            return re.sub(pattern, '', row['Quality Characteristics']).strip()
        return row['Quality Characteristics']

    df['Results_clean'] = df.apply(clean_results, axis=1)
    df['Quality Characteristics'] = df.apply(clean_param, axis=1)

    # Create 'Param_with_unit' column
    df['Param_with_unit'] = df["Quality Characteristics"].str.strip() + df["Unit_extracted"].apply(lambda x: f",{x.strip()}" if pd.notna(x) else "")


    # Display the updated dataframe
    return df


# Function to extract specific keys from a nested JSON structure
def find_keys(data, keys):
    results = []
    if isinstance(data, dict):
        extracted_values = {key: data.get(key, "") for key in keys if key in data and data[key] != ""}
        if extracted_values:
            results.append(extracted_values)
        for value in data.values():
            results.extend(find_keys(value, keys))
    elif isinstance(data, list):
        for item in data:
            results.extend(find_keys(item, keys))
    return results

# Define a single list of all possible keys across different JSON files
all_keys = ["Quality Characteristics","Results","Method of test","Units","Prescribed Limit by FSSR","LOQ"]
opinion_keys = ["OpinionRemarks", "Opinion", "Remarks"]

In [10]:
def json_to_csv_2(file_name):
    # Open and read the JSON file    
    with open(file_name, 'r',encoding='utf8') as file:
        data = json.load(file)
    # Print the data
    # print(data)
    main_keys = list(data.keys())
    print(main_keys)

    temp = pd.DataFrame()
    print(len(data[main_keys[-1]]))
    resultstable = data[main_keys[-1]]


    # for i, j in enumerate (data[main_keys[-1]]):
    #     # print(i, j)
    #     d0 = pd.DataFrame([j])
    #     temp = pd.concat([temp, d0], ignore_index= True)
        
    
    # Extract required data
    extracted_data = find_keys(resultstable, all_keys)

    if extracted_data:  # Only process if data exists
    # Convert to DataFrame
        temp = pd.DataFrame(extracted_data)

        # Remove empty columns (columns with all NaN values)
        # temp = temp.dropna(axis=1, how="all")

   
    #save report number
    # temp[main_keys[1]] = #data.get(main_keys[1])


    #Extract order id from file name
    order_id = file_name.split('\\')[-1].split('.')[0]
    temp['Order ID'] = order_id
    # 'D:\\Biswajit\\FSSAI\\jsontocsv\\turmeric\\Bvi\\consumed\\FS-AP-SR-TURMERIC_WHOLE-028846_output.json'
    #save Opinion Remarks; adding report number with opinion for identification in future
    temp[main_keys[2]]= ""# 
    # oi = temp.shape[1]
    OpinionRemarks = str(main_keys[2])
    temp.loc[0, OpinionRemarks ] = str(data.get(main_keys[2])) #data.get(main_keys[1]) + ' : ' 

    # df_bvi=pd.read_csv(r"D:\Biswajit\FSSAI\jsontocsv\bvi_updated.json.csv")
    df_bvi = temp
    df_bvi = unit_cleaning(df_bvi)


    return df_bvi

In [12]:
# csv_files = [f for f in os.listdir(jsondir) if f.endswith('.json')]
json_files = glob.glob(f"{jsondir}/*.json")
# json_files

# Conver all json files to csv
temp1 = pd.DataFrame()
for i,j in enumerate(json_files):
    print(i,j)
    
    df_bvi1 = pd.DataFrame()
    try:
        df_bvi1 = json_to_csv_2(j)
        # print(df_bvi1['ReportNumber'].unique())
        temp1 = pd.concat([temp1, df_bvi1], ignore_index= True)
    except:
        print('file not processed', j)


# temp1.to_csv(str(jsondir.split('\\')[-1])+'.csv', index=False)
temp1.to_excel(str(jsondir.split('\\')[-1])+'Dj_test'+'.xlsx', index=False)
print('shape after json2csv', temp1.shape)

0 D:\Dev_Playground\10_march\processed_outputs\000311_report_FS-KL-PA-TURMERIC_POWDER-126904.json
['AgnextHeader', 'ReportNumber', 'OpinionRemarks', 'AllTableResults']
252
1 D:\Dev_Playground\10_march\processed_outputs\0310_report_FS-KA-BE-TURMERIC_WHOLE-152295.json
['AgnextHeader', 'ReportNumber', 'OpinionRemarks', 'AllTableResults']
270
2 D:\Dev_Playground\10_march\processed_outputs\1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683.json
['AgnextHeader', 'ReportNumber', 'OpinionRemarks', 'AllTableResults']
105
3 D:\Dev_Playground\10_march\processed_outputs\1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670.json
['AgnextHeader', 'ReportNumber', 'OpinionRemarks', 'AllTableResults']
105
4 D:\Dev_Playground\10_march\processed_outputs\1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665.json
['AgnextHeader', 'ReportNumber', 'OpinionRemarks', 'AllTableResults']
105
5 D:\Dev_Playground\10_march\processed_outputs\1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423.json
['AgnextHeader', 'ReportNumber', 

In [13]:
temp1.head()

Quality Characteristics Results      Method of test    Units  \
0                    Salmonella  Absent   ISO 6579-1 : 2017  Per 25g   
1           Yeast & Mould Count     <10  ISO 21527-2 : 2008    CFU/g   
2            Enterobacteriaceae     <10   ISO 21528-2: 2017    CFU/g   
3         Staphylococcus aureus     <10   ISO 6888-1 : 2021    CFU/g   
4  Sulphite Reducing Clostridia     <10  ISO 15213-1 : 2023    CFU/g   

  Prescribed Limit by FSSR   LOQ  \
0                   Absent  None   
1          m=1x10\nM=1x10⁵  None   
2          m=1x10\nM=1x10³  None   
3          m=1x10\nM=1x10³  None   
4          m=1x10\nM=1x10³  None   

                                        Order ID  \
0  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
1  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
2  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
3  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
4  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   

                                      OpinionRemarks Unit_extracted  \
0  The sample sent for analysis conforms to the s...        Per 25g   
1                                                             CFU/g   
2                                                             CFU/g   
3                                                             CFU/g   
4                                                             CFU/g   

  Results_clean                     Param_with_unit  
0        Absent                  Salmonella,Per 25g  
1           <10           Yeast & Mould Count,CFU/g  
2           <10            Enterobacteriaceae,CFU/g  
3           <10         Staphylococcus aureus,CFU/g  
4           <10  Sulphite Reducing Clostridia,CFU/g

In [14]:
temp1

Quality Characteristics    Results            Method of test  \
0                       Salmonella     Absent         ISO 6579-1 : 2017   
1              Yeast & Mould Count        <10        ISO 21527-2 : 2008   
2               Enterobacteriaceae        <10         ISO 21528-2: 2017   
3            Staphylococcus aureus        <10         ISO 6888-1 : 2021   
4     Sulphite Reducing Clostridia        <10        ISO 15213-1 : 2023   
...                            ...        ...                       ...   
8181            Enterobacteriaceae        150       ISO:21528(P-2):2017   
8182                   Salmonella,     Absent  IS:5887(P-3)(Sec-1):2020   
8183   Sulfite reducing clostridia        <10       ISO:15123(P-1):2023   
8184               Bacillus Cereus        <10         IS:5887(P-6):2012   
8185           Aerobic Plate Count  2.43*10^4         IS:5402(P-1):2021   

        Units Prescribed Limit by FSSR   LOQ  \
0     Per 25g                   Absent  None   
1       CFU/g          m=1x10\nM=1x10⁵  None   
2       CFU/g          m=1x10\nM=1x10³  None   
3       CFU/g          m=1x10\nM=1x10³  None   
4       CFU/g          m=1x10\nM=1x10³  None   
...       ...                      ...   ...   
8181    cfu/g               Max 1X10^3  None   
8182  Per 25g                   Absent  None   
8183    cfu/g               Max 1X10^3  None   
8184    cfu/g               Max 1X10^4  None   
8185    cfu/g               Max 1X10^7  None   

                                               Order ID  \
0         000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
1         000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
2         000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
3         000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
4         000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
...                                                 ...   
8181  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
8182  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
8183  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
8184  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
8185  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   

                                         OpinionRemarks Unit_extracted  \
0     The sample sent for analysis conforms to the s...        Per 25g   
1                                                                CFU/g   
2                                                                CFU/g   
3                                                                CFU/g   
4                                                                CFU/g   
...                                                 ...            ...   
8181                                                             cfu/g   
8182                                                           Per 25g   
8183                                                             cfu/g   
8184                                                             cfu/g   
8185                                                             cfu/g   

     Results_clean                     Param_with_unit  
0           Absent                  Salmonella,Per 25g  
1              <10           Yeast & Mould Count,CFU/g  
2              <10            Enterobacteriaceae,CFU/g  
3              <10         Staphylococcus aureus,CFU/g  
4              <10  Sulphite Reducing Clostridia,CFU/g  
...            ...                                 ...  
8181           150            Enterobacteriaceae,cfu/g  
8182        Absent                 Salmonella,,Per 25g  
8183           <10   Sulfite reducing clostridia,cfu/g  
8184           <10               Bacillus Cereus,cfu/g  
8185     2.43*10^4           Aerobic Plate Count,cfu/g  

[8186 rows x 11 columns]

In [15]:
temp1 = temp1.dropna(subset='Param_with_unit')


In [16]:
temp1.shape

(8176, 11)

Master Sheet preparation

In [23]:
m= pd.read_excel(r'D:\Dev_Playground\10_march\Master Parameters.xlsx', sheet_name='Matching_Template')
print(m.shape)
# m.head()
m['Param_with_unit (From Report)'] = m['Param_with_unit (From Report)'].str.lower().str.replace('\n','', regex=False)
m1 = m.drop_duplicates(subset=['Param_with_unit (From Report)'])
m1 = m1.drop(columns=['Iteration'])
print(m1.shape)
m1.rename(columns={'Param_with_unit (From Report)':'Param_with_unit' }, inplace=True)
m1.reset_index(inplace=True,drop=True)

# m1 = m1['Param_with_unit'].str.replace('\n','', regex=False)
# m1.head()

(8131, 3)
(4550, 2)


In [25]:
# m1.to_excel('master_0902251318.xlsx')
# pd.DataFrame(m1['Master'].unique()).to_excel('master_uniqes.xlsx', index=False)
m1.head()

Param_with_unit  \
0      fenvalerate (fat soluble residue)   
1                 2,4 d amine salt,mg/kg   
2                            2,4 d,mg/kg   
3                 2,4-d amine salt,mg/kg   
4  2,4 dichlorophenoxy acetic acid,mg/kg   

                                    Master  
0  Fenvalerate (Fat soluble residue),mg/kg  
1                   2,4-D Amine Salt,mg/kg  
2    2,4-Dichlorophenoxy Acetic Acid,mg/kg  
3                   2,4-D Amine Salt,mg/kg  
4    2,4-Dichlorophenoxy Acetic Acid,mg/kg

In [26]:
# master = pd.read_excel("D:\Biswajit\FSSAI\param_matching\Master Parameters.xlsx", sheet_name='bpp')
# master = pd.read_excel("D:\Biswajit\FSSAI\param_matching\master.xlsx")
master = m1
# report = pd.read_excel('D:\Biswajit\FSSAI\param_matching\processed_outputs_bpp.xlsx',sheet_name='INHYD24086851129042740')
report = temp1#[temp1['ReportNumber']=='01/ETHFSR2401209, 02/ETHFSR2401209']
# report
df_final = param_matching(master,report)
# df_final.to_excel(str(jsondir.split('\\')[-1])+'after_mapping-190225-noon.xlsx', index=False)

Report parameters: (8176, 11)
Matched by Direct mapping:  (7998, 12)
Fuzzy required
Need to match with fuzzy: (178, 12)


In [27]:
df_final.isna().sum()

Quality Characteristics        0
Results                        8
Method of test               984
Units                        566
Prescribed Limit by FSSR     293
LOQ                         3313
Order ID                       0
OpinionRemarks                 0
Unit_extracted               588
Results_clean                  8
Param_with_unit                0
Master                       178
param_with_unit_alias       7998
master_param                7998
matching_score              7998
review-suggest              7998
dtype: int64

#### Adding Master param for cases having score>92%

In [18]:
df_final.loc[df_final['matching_score'] > 92, 'Master'] = df_final['master_param']

In [19]:
df_final.isna().sum()

Quality Characteristics        0
Results                        8
Method of test               984
Units                        566
Prescribed Limit by FSSR     293
Order ID                       0
OpinionRemarks                 0
Unit_extracted               588
Results_clean                  8
Param_with_unit                0
Master                        32
param_with_unit_alias       7998
master_param                7998
matching_score              7998
review-suggest              7998
dtype: int64

In [28]:
df_final1 = df_final.dropna(subset='matching_score').drop_duplicates(subset=['Param_with_unit'])

print(df_final1.shape, df_final.shape)

df_final1.to_excel(str(jsondir.split('\\')[-1])+f'after_mapping-{commodity}-190225.xlsx', index=False)

(151, 16) (8176, 16)


In [29]:
df_final.head()

Quality Characteristics      Results  \
0  Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1                Extraneous matter         0.18   
2         Unripe and marked fruit,         0.38   
3  Broken fruits, seed & fragment,          1.8   
4        Total ash (on dry basis),         6.20   

                                      Method of test        Units  \
0  FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
2     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
3     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4     FSSAI 10.006.2021\n(Spices Herbs & Condiments)  % by weight   

  Prescribed Limit by FSSR   LOQ  \
0                   Absent  None   
1        Not more than 1.0  None   
2        Not more than 2.0  None   
3        Not more than 5.0  None   
4        Not more than 8.0  None   

                                            Order ID OpinionRemarks  \
0         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
2  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
3  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  

  Unit_extracted Results_clean                              Param_with_unit  \
0              %   BLQ of 0.01            rodent/animal/mammalian excreta,%   
1    % by weight          0.18                extraneous matter,% by weight   
2    % by weight          0.38         unripe and marked fruit,,% by weight   
3    % by weight           1.8  broken fruits, seed & fragment,,% by weight   
4    % by weight          6.20        total ash (on dry basis),,% by weight   

  Master                       param_with_unit_alias  \
0    NaN             rodent/animal/maalian excreta,%   
1    NaN              extraneous matter, % by weight   
2    NaN         unripe and marked fruit,by weight,%   
3    NaN  broken fruits, seed & fragment,by weight,%   
4    NaN                 total ash (on dry basis),,%   

                                        master_param  matching_score  \
0  Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
1                                Extraneous matter,%           98.31   
2                         Unripe and marked fruits,%           92.96   
3                  Broken fruits, seed & fragments,%           94.12   
4                         Total ash (on dry basis),%           95.00   

  review-suggest  
0        matched  
1        matched  
2        matched  
3        matched  
4        matched

This is the DF with LOQ

In [30]:
df_final

Quality Characteristics      Results  \
0     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1                   Extraneous matter         0.18   
2            Unripe and marked fruit,         0.38   
3     Broken fruits, seed & fragment,          1.8   
4           Total ash (on dry basis),         6.20   
...                               ...          ...   
8171               Enterobacteriaceae          150   
8172                      Salmonella,       Absent   
8173      Sulfite reducing clostridia          <10   
8174                  Bacillus Cereus          <10   
8175              Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
2        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4        FSSAI 10.006.2021\n(Spices Herbs & Condiments)  % by weight   
...                                                 ...          ...   
8171                                ISO:21528(P-2):2017        cfu/g   
8172                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8173                                ISO:15123(P-1):2023        cfu/g   
8174                                  IS:5887(P-6):2012        cfu/g   
8175                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
1           Not more than 1.0  None   
2           Not more than 2.0  None   
3           Not more than 5.0  None   
4           Not more than 8.0  None   
...                       ...   ...   
8171               Max 1X10^3  None   
8172                   Absent  None   
8173               Max 1X10^3  None   
8174               Max 1X10^4  None   
8175               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
2     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
...                                                 ...            ...   
8171  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8172  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8173  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8174  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8175  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  \
0                 %   BLQ of 0.01   
1       % by weight          0.18   
2       % by weight          0.38   
3       % by weight           1.8   
4       % by weight          6.20   
...             ...           ...   
8171          cfu/g           150   
8172        Per 25g        Absent   
8173          cfu/g           <10   
8174          cfu/g           <10   
8175          cfu/g     2.43*10^4   

                                  Param_with_unit  \
0               rodent/animal/mammalian excreta,%   
1                   extraneous matter,% by weight   
2            unripe and marked fruit,,% by weight   
3     broken fruits, seed & fragment,,% by weight   
4           total ash (on dry basis),,% by weight   
...                                           ...   
8171                     enterobacteriaceae,cfu/g   
8172                          salmonella,,per 25g   
8173            sulfite reducing clostridia,cfu/g   
8174                        bacillus cereus,cfu/g   
8175                    aerobic plate count,cfu/g   

                                 Master  \
0                

In [32]:
m_with_units= pd.read_excel(r'D:\Dev_Playground\10_march\Master Parameters.xlsx', sheet_name='Master')
m_with_units1 = m_with_units[['mathcing_param','Units']]
m_with_units1.rename(columns={'mathcing_param':'Master' }, inplace=True)
m_with_units1.rename(columns={'Units':'Master_Units' }, inplace=True)
m_with_units1.head()


Master Master_Units
0  Added Colouring Matter,mg/kg        mg/kg
1            Aflatoxin B1,µg/kg        µg/kg
2           Arsenic as As,mg/kg        mg/kg
3           Cadmium as Cd,mg/kg        mg/kg
4            Copper as Cu,mg/kg        mg/kg

In [33]:
print(m_with_units1.shape)
m_with_units2 = m_with_units1.drop_duplicates(subset='Master')
print(m_with_units2.shape)


(3587, 2)
(333, 2)


In [34]:
df_final.columns

Index(['Quality Characteristics', 'Results', 'Method of test', 'Units',
       'Prescribed Limit by FSSR', 'LOQ', 'Order ID', 'OpinionRemarks',
       'Unit_extracted', 'Results_clean', 'Param_with_unit', 'Master',
       'param_with_unit_alias', 'master_param', 'matching_score',
       'review-suggest'],
      dtype='object')

In [35]:
df_final.head()

Quality Characteristics      Results  \
0  Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1                Extraneous matter         0.18   
2         Unripe and marked fruit,         0.38   
3  Broken fruits, seed & fragment,          1.8   
4        Total ash (on dry basis),         6.20   

                                      Method of test        Units  \
0  FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
2     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
3     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4     FSSAI 10.006.2021\n(Spices Herbs & Condiments)  % by weight   

  Prescribed Limit by FSSR   LOQ  \
0                   Absent  None   
1        Not more than 1.0  None   
2        Not more than 2.0  None   
3        Not more than 5.0  None   
4        Not more than 8.0  None   

                                            Order ID OpinionRemarks  \
0         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
2  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
3  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  

  Unit_extracted Results_clean                              Param_with_unit  \
0              %   BLQ of 0.01            rodent/animal/mammalian excreta,%   
1    % by weight          0.18                extraneous matter,% by weight   
2    % by weight          0.38         unripe and marked fruit,,% by weight   
3    % by weight           1.8  broken fruits, seed & fragment,,% by weight   
4    % by weight          6.20        total ash (on dry basis),,% by weight   

  Master                       param_with_unit_alias  \
0    NaN             rodent/animal/maalian excreta,%   
1    NaN              extraneous matter, % by weight   
2    NaN         unripe and marked fruit,by weight,%   
3    NaN  broken fruits, seed & fragment,by weight,%   
4    NaN                 total ash (on dry basis),,%   

                                        master_param  matching_score  \
0  Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
1                                Extraneous matter,%           98.31   
2                         Unripe and marked fruits,%           92.96   
3                  Broken fruits, seed & fragments,%           94.12   
4                         Total ash (on dry basis),%           95.00   

  review-suggest  
0        matched  
1        matched  
2        matched  
3        matched  
4        matched

In [36]:
df_final

Quality Characteristics      Results  \
0     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1                   Extraneous matter         0.18   
2            Unripe and marked fruit,         0.38   
3     Broken fruits, seed & fragment,          1.8   
4           Total ash (on dry basis),         6.20   
...                               ...          ...   
8171               Enterobacteriaceae          150   
8172                      Salmonella,       Absent   
8173      Sulfite reducing clostridia          <10   
8174                  Bacillus Cereus          <10   
8175              Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
2        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4        FSSAI 10.006.2021\n(Spices Herbs & Condiments)  % by weight   
...                                                 ...          ...   
8171                                ISO:21528(P-2):2017        cfu/g   
8172                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8173                                ISO:15123(P-1):2023        cfu/g   
8174                                  IS:5887(P-6):2012        cfu/g   
8175                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
1           Not more than 1.0  None   
2           Not more than 2.0  None   
3           Not more than 5.0  None   
4           Not more than 8.0  None   
...                       ...   ...   
8171               Max 1X10^3  None   
8172                   Absent  None   
8173               Max 1X10^3  None   
8174               Max 1X10^4  None   
8175               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
2     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
...                                                 ...            ...   
8171  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8172  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8173  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8174  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8175  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  \
0                 %   BLQ of 0.01   
1       % by weight          0.18   
2       % by weight          0.38   
3       % by weight           1.8   
4       % by weight          6.20   
...             ...           ...   
8171          cfu/g           150   
8172        Per 25g        Absent   
8173          cfu/g           <10   
8174          cfu/g           <10   
8175          cfu/g     2.43*10^4   

                                  Param_with_unit  \
0               rodent/animal/mammalian excreta,%   
1                   extraneous matter,% by weight   
2            unripe and marked fruit,,% by weight   
3     broken fruits, seed & fragment,,% by weight   
4           total ash (on dry basis),,% by weight   
...                                           ...   
8171                     enterobacteriaceae,cfu/g   
8172                          salmonella,,per 25g   
8173            sulfite reducing clostridia,cfu/g   
8174                        bacillus cereus,cfu/g   
8175                    aerobic plate count,cfu/g   

                                 Master  \
0                

In [22]:
# df_final.loc[df_final['matching_score'] > 92, 'Master'] = df_final['master_param']

In [38]:
df_final_units = pd.merge(df_final,m_with_units2,on='Master',how='left')

df_final_units["compare_unit"] = df_final_units.apply(lambda row: "same" if row["Unit_extracted"] == row["Master_Units"] else "difference", axis=1)
# df_final_units.loc[df_final_units['matching_score'] > 92, 'Master'] = df_final_units['master_param']
df_final_units.to_excel(str(jsondir.split('\\')[-1])+'after_mapping_units_Dj_test.xlsx', index=False)
# df_final_units.

In [39]:
df_final_units.columns

Index(['Quality Characteristics', 'Results', 'Method of test', 'Units',
       'Prescribed Limit by FSSR', 'LOQ', 'Order ID', 'OpinionRemarks',
       'Unit_extracted', 'Results_clean', 'Param_with_unit', 'Master',
       'param_with_unit_alias', 'master_param', 'matching_score',
       'review-suggest', 'Master_Units', 'compare_unit'],
      dtype='object')

In [40]:
param_to_db = pd.read_excel('Master Parameters.xlsx', sheet_name='Matching_Template_db')
param_to_db.head()

Master Parameter Name (Google Sheet)  Unnamed: 2  \
0  Added Colouring Matter,mg/kg        Added Colouring Matter         NaN   
1            Aflatoxin B1,µg/kg           Aflatoxin B1, µg/kg         NaN   
2           Arsenic as As,mg/kg          Arsenic as As, mg/kg         NaN   
3           Cadmium as Cd,mg/kg          Cadmium as Cd, mg/kg         NaN   
4            Copper as Cu,mg/kg           Copper as Cu, mg/kg         NaN   

       Parameter_Key_DB Parameter Name (Google Sheet)_seq  
0  addedColouringMatter            Added Colouring Matter  
1       aflatoxinB1Μgkg               Aflatoxin B1, µg/kg  
2       arsenicAsAsMgkg              Arsenic as As, mg/kg  
3       cadmiumAsCdMgkg              Cadmium as Cd, mg/kg  
4        copperAsCuMgkg               Copper as Cu, mg/kg

In [41]:
df_db = pd.merge(df_final,param_to_db,on='Master',how='left')
df_db.head()

Quality Characteristics      Results  \
0  Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1  Rodent/Animal/Mammalian excreta  BLQ of 0.01   
2  Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                Extraneous matter         0.18   
4                Extraneous matter         0.18   

                                      Method of test        Units  \
0  FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1  FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
2  FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   

  Prescribed Limit by FSSR   LOQ  \
0                   Absent  None   
1                   Absent  None   
2                   Absent  None   
3        Not more than 1.0  None   
4        Not more than 1.0  None   

                                            Order ID OpinionRemarks  \
0         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
2         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  

  Unit_extracted Results_clean                    Param_with_unit Master  \
0              %   BLQ of 0.01  rodent/animal/mammalian excreta,%    NaN   
1              %   BLQ of 0.01  rodent/animal/mammalian excreta,%    NaN   
2              %   BLQ of 0.01  rodent/animal/mammalian excreta,%    NaN   
3    % by weight          0.18      extraneous matter,% by weight    NaN   
4    % by weight          0.18      extraneous matter,% by weight    NaN   

             param_with_unit_alias  \
0  rodent/animal/maalian excreta,%   
1  rodent/animal/maalian excreta,%   
2  rodent/animal/maalian excreta,%   
3   extraneous matter, % by weight   
4   extraneous matter, % by weight   

                                        master_param  matching_score  \
0  Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
1  Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
2  Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
3                                Extraneous matter,%           98.31   
4                                Extraneous matter,%           98.31   

  review-suggest Parameter Name (Google Sheet)  Unnamed: 2  \
0        matched                           NaN         NaN   
1        matched                           NaN         NaN   
2        matched                           NaN         NaN   
3        matched                           NaN         NaN   
4        matched                           NaN         NaN   

      Parameter_Key_DB Parameter Name (Google Sheet)_seq  
0        metanilYellow          Other harmful substances  
1  testForLeadChromate                            Starch  
2          addedStarch                               NaN  
3        metanilYellow          Other harmful substances  
4  testForLeadChromate                            Starch

In [42]:
len(df_db['Parameter Name (Google Sheet)'].unique())

297

In [46]:
df_db_final = df_db.copy()


In [47]:
# df_db_final = df_db[['Order ID','Parameter Name (Google Sheet)','Results_clean', 'Unit_extracted',]]
print(df_db_final.shape)
df_db_final = df_db_final.drop_duplicates(subset=['Order ID','Parameter Name (Google Sheet)'])
df_db_final.to_excel('df_db_final_Dj_test.xlsx')
# df_db_final.dropna(subset=['Parameter Name (Google Sheet)'], inplace=True)
print(df_db_final.shape)
df_db_final.head()

(8532, 20)
(7788, 20)


Quality Characteristics      Results  \
0                     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                   Extraneous matter         0.18   
30                                  Extraneous matter         0.27   
57                                  Extraneous matter         0.20   
84  Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   

                                       Method of test        Units  \
0   FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3      FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57     FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84  FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   

   Prescribed Limit by FSSR   LOQ  \
0                    Absent  None   
3         Not more than 1.0  None   
30        Not more than 1.0  None   
57        Not more than 1.0  None   
84                   Absent  None   

                                             Order ID OpinionRemarks  \
0          0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3   1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30  1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57   1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84     1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  

   Unit_extracted Results_clean  \
0               %   BLQ of 0.01   
3     % by weight          0.18   
30    % by weight          0.27   
57    % by weight          0.20   
84              %   BLQ of 0.01   

                                      Param_with_unit Master  \
0                   rodent/animal/mammalian excreta,%    NaN   
3                       extraneous matter,% by weight    NaN   
30                      extraneous matter,% by weight    NaN   
57                      extraneous matter,% by weight    NaN   
84  dead insects, insect fragments, rodent/animal/...    NaN   

                                param_with_unit_alias  \
0                     rodent/animal/maalian excreta,%   
3                      extraneous matter, % by weight   
30                     extraneous matter, % by weight   
57                     extraneous matter, % by weight   
84  dead insects, insect fragments, rodent/animal/...   

                                         master_param  matching_score  \
0   Dirt, dust, straw, insect, damaged seeds, othe...           96.88   
3                                 Extraneous matter,%           98.31   
30                                Extraneous matter,%           98.31   
57                                Extraneous matter,%           98.31   
84     Live insects, Dead Insects, Insect Fragments,%           97.08   

   review-suggest Parameter Name (Google Sheet)  Unnamed: 2 Parameter_Key_DB  \
0         matched                           NaN         NaN    metanilYellow   
3         matched                           NaN         NaN    metanilYellow   
30        matched                           NaN         NaN    metanilYellow   
57        matched                           NaN         NaN    metanilYellow   
84        matched                           NaN         NaN    metanilYellow   

   Parameter Name (Google Sheet)_seq  
0           Other harmful substances  
3           Other harmful substances  
30          Other harmful substances  
57          Other harmful substances  
84          Other harmful substances

### Convert Results to required values

In [48]:
import re
import numpy as np

# Mapping superscript characters to normal digits
superscript_map = str.maketrans("⁰¹²³⁴⁵⁶⁷⁸⁹", "0123456789")

def parse_result(value):
    val_str = str(value).strip().lower()
    val_str = val_str.translate(superscript_map)  # Convert superscript numbers

    # Normalize formats like "4.7x x10(5)" → "4.7 x 10^5"
    val_str = re.sub(r"\s*x\s*x\s*", " x ", val_str)  # Fix double "x"
    val_str = re.sub(r"10\((\d+)\)", r"10^\1", val_str)  # Convert 10(5) → 10^5

    # First, check for normal multiplication (e.g., "1.88 x 1000")
    match_multiply = re.search(r"([\d\.]+)\s*[xX×*]\s*(10+)$", val_str)
    if match_multiply:
        base = float(match_multiply.group(1))
        multiplier = int(match_multiply.group(2))  # Convert to an integer
        return np.multiply(base, multiplier)  # Use NumPy for multiplication

    # Then, check for scientific notation (X x 10^Y OR X x 10Y where Y is 1-9)
    match_sci = re.search(r"([\d\.]+)\s*[xX×*]\s*10\^?(\d+)", val_str)
    if match_sci:
        base = float(match_sci.group(1))
        exponent = int(match_sci.group(2))
        return base * (10 ** exponent)

   

def convert_result(report_value):
    report_value = str(report_value).strip().replace('\n','')
    
    # Keywords mapping to 0
    if report_value.lower() in ['absent', 'negative', 'nil', 'conform/s', 'compile/s','absenl','complies','not detected','absenl','-absent','conforms','free']\
          or report_value.lower().startswith('free from') or 'it is free from' in report_value.lower() or 'absent' in report_value.lower()\
           or 'free from' in report_value.lower() or 'not observed' in report_value.lower() or'freee from' in report_value.lower():
        return 0.0
    # Keywords mapping to 1
    elif report_value.lower() in ['present', 'positive'] or report_value.lower().startswith('present'):
        return 1.0
    # Handle BLQ 
    elif 'BL' in report_value:
        pattern = re.compile(r'(?:LOQ:?\s*|<|DL:|of\s*|\s*)(\d+\.?\d*)')
        match = pattern.search(report_value)
        if match:
            extracted_num = match.group(1)
            if '.' in extracted_num:
                num = float(extracted_num)
            else:
                num = int(extracted_num) / 10  # Assume no decimal implies thousandths
            return num / 10
        else:
            return 0.0001
          # Default for BLQ without specific value
    elif 'B.L.Q' in report_value or '(Q.L.=' in report_value:
        match = re.search(r'\(Q\.L\.*\s*=?\s*([\d\.]+)\)', report_value)
        if match:
            try:
                extracted_num = float(match.group(1))
                return extracted_num / 10  # Convert QL to result
            except ValueError:
                return None
                # Default for BLQ without specific value
        
    elif report_value.startswith('ND') or report_value.startswith('BDL'):
        # Regex to match variations like "DL: X", "DL : X", "DL X"
        pattern = re.compile(r'DL[: ]*\s*(\d+\.?\d*)')
        match = pattern.search(report_value)
        if match:
            extracted_num = float(match.group(1))
            return extracted_num / 10
    elif 'bql' in report_value.lower():
        return 0.0001
    # Handle "Less Than X" cases
    match_less_than = re.search(r'less\s*than\s*([\d\.]+)', report_value.lower())
    if match_less_than:
        extracted_num = float(match_less_than.group(1))
        return extracted_num / 10  # Convert by dividing by 10
   # Handle "<100 m" or similar cases
    match_m = re.search(r'<\s*(\d+)\s*m?', report_value)
    if match_m:
        extracted_num = float(match_m.group(1))
        return extracted_num / 10  # Convert by dividing by 10
    
    # Use parse_result function for scientific notation & multiplication cases
    parsed_value = parse_result(report_value)
    if parsed_value is not None:
        return parsed_value
    # Handle percentages
    elif '%' in report_value:
        return float(report_value.replace('%', ''))
    elif '()' in report_value:
        return float(report_value.replace('()', ''))
    elif report_value.endswith('*'):
        try:
            return float(report_value.replace('*', ''))
        except ValueError:
            return None
    # elif report_value.endswith('m'):
    #     return float(report_value.replace('m', ''))
        

    # # Handle values starting with '<'
    # elif report_value.startswith('<'):
    #     try:
    #         return float(report_value[1:]) / 10
    #     except ValueError:
    #         return report_value + str(',404') 

    # Try converting directly to float
    else:
        try:
            return float(report_value)
        except ValueError:
            if ',' in report_value and len(report_value)>5:
                try:
                    return float(report_value.replace(',',''))
                except ValueError:
                    return None # Default for unexpected formats


In [49]:
#Conversion from text to numeric based on conversion logic
df_db_final['Required_Results'] = df_db_final['Results_clean'].apply(convert_result)
df_db['OpinionRemarks'].replace("",None,inplace=True)


In [50]:
df_db_final

Quality Characteristics      Results  \
0                       Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                     Extraneous matter         0.18   
30                                    Extraneous matter         0.27   
57                                    Extraneous matter         0.20   
84    Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   
...                                                 ...          ...   
8527                                 Enterobacteriaceae          150   
8528                                        Salmonella,       Absent   
8529                        Sulfite reducing clostridia          <10   
8530                                    Bacillus Cereus          <10   
8531                                Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30       FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57       FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84    FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   
...                                                 ...          ...   
8527                                ISO:21528(P-2):2017        cfu/g   
8528                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8529                                ISO:15123(P-1):2023        cfu/g   
8530                                  IS:5887(P-6):2012        cfu/g   
8531                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
3           Not more than 1.0  None   
30          Not more than 1.0  None   
57          Not more than 1.0  None   
84                     Absent  None   
...                       ...   ...   
8527               Max 1X10^3  None   
8528                   Absent  None   
8529               Max 1X10^3  None   
8530               Max 1X10^4  None   
8531               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30    1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57     1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84       1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  
...                                                 ...            ...   
8527  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8528  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8529  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8530  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8531  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  ...                             Master  \
0                 %   BLQ of 0.01  ...                                NaN   
3       % by weight          0.18  ...                                NaN   
30      % by weight          0.27  ...                                NaN   
57      % by weight          0.20  ...                                NaN   
84                %   BLQ of 0.01  ...                                NaN   
...             ...           ...  ...                                ...   
8527          cfu/g           150  ...           Enterobacteriaceae,CFU/g   
8528        Per 25g        Absent  ...                 Salmonella,Per 25g   
8529          cfu/g           <10  ...  Sulfite reducing clostridia,CFU/g   
8530          cfu/g           <10  ...              Bacillus Cereus,CFU/g   
8531          cfu/g     2.43*10^4  ...          Aerobic Plate Count,CFU/g   

                   

In [45]:
df_db

Quality Characteristics      Results  \
0     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
1     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
2     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                   Extraneous matter         0.18   
4                   Extraneous matter         0.18   
...                               ...          ...   
8527               Enterobacteriaceae          150   
8528                      Salmonella,       Absent   
8529      Sulfite reducing clostridia          <10   
8530                  Bacillus Cereus          <10   
8531              Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
1     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
2     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
4        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
...                                                 ...          ...   
8527                                ISO:21528(P-2):2017        cfu/g   
8528                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8529                                ISO:15123(P-1):2023        cfu/g   
8530                                  IS:5887(P-6):2012        cfu/g   
8531                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
1                      Absent  None   
2                      Absent  None   
3           Not more than 1.0  None   
4           Not more than 1.0  None   
...                       ...   ...   
8527               Max 1X10^3  None   
8528                   Absent  None   
8529               Max 1X10^3  None   
8530               Max 1X10^4  None   
8531               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
1            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
2            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
4     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
...                                                 ...            ...   
8527  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8528  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8529  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8530  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8531  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean                    Param_with_unit  \
0                 %   BLQ of 0.01  rodent/animal/mammalian excreta,%   
1                 %   BLQ of 0.01  rodent/animal/mammalian excreta,%   
2                 %   BLQ of 0.01  rodent/animal/mammalian excreta,%   
3       % by weight          0.18      extraneous matter,% by weight   
4       % by weight          0.18      extraneous matter,% by weight   
...             ...           ...                                ...   
8527          cfu/g           150           enterobacteriaceae,cfu/g   
8528        Per 25g        Absent                salmonella,,per 25g   
8529          cfu/g           <10  sulfite reducing clostridia,cfu/g   
8530          cfu/g           <10              bacillus cereus,cfu/g   
8531          cfu/g     2.43*10^4          aerobic plate count,cfu/g   

                                 Master            param_with_unit_alias  \
0                                   NaN  rodent/animal/maalian excreta,%   
1                                   NaN  rodent/animal/maalian excreta,%   
2                                   NaN  rodent/a

In [51]:

# Creating the new column by appending Unit_extracted if it's not None or empty
df_db_final['Results_with_units'] = df_db_final.apply(
    lambda row: f"{row['Results_clean']}, {row['Unit_extracted']}" if pd.notna(row['Unit_extracted']) and row['Unit_extracted'] else row['Results_clean'],
    axis=1
)


# df_db_final['Results_with_units']
df_db_final.shape

(7788, 22)

In [52]:
df_db_final

Quality Characteristics      Results  \
0                       Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                     Extraneous matter         0.18   
30                                    Extraneous matter         0.27   
57                                    Extraneous matter         0.20   
84    Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   
...                                                 ...          ...   
8527                                 Enterobacteriaceae          150   
8528                                        Salmonella,       Absent   
8529                        Sulfite reducing clostridia          <10   
8530                                    Bacillus Cereus          <10   
8531                                Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30       FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57       FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84    FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   
...                                                 ...          ...   
8527                                ISO:21528(P-2):2017        cfu/g   
8528                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8529                                ISO:15123(P-1):2023        cfu/g   
8530                                  IS:5887(P-6):2012        cfu/g   
8531                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
3           Not more than 1.0  None   
30          Not more than 1.0  None   
57          Not more than 1.0  None   
84                     Absent  None   
...                       ...   ...   
8527               Max 1X10^3  None   
8528                   Absent  None   
8529               Max 1X10^3  None   
8530               Max 1X10^4  None   
8531               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30    1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57     1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84       1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  
...                                                 ...            ...   
8527  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8528  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8529  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8530  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8531  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  ...  \
0                 %   BLQ of 0.01  ...   
3       % by weight          0.18  ...   
30      % by weight          0.27  ...   
57      % by weight          0.20  ...   
84                %   BLQ of 0.01  ...   
...             ...           ...  ...   
8527          cfu/g           150  ...   
8528        Per 25g        Absent  ...   
8529          cfu/g           <10  ...   
8530          cfu/g           <10  ...   
8531          cfu/g     2.43*10^4  ...   

                                  param_with_unit_alias  \
0                       rodent/animal/maalian excreta,%   
3                        extraneous matter, % by weight   
30                       extraneous matter, % by weight   
57                       extraneous matter, % by weight   
84    dead insects, insect fragments, rodent/animal/...   
...                                                 ...   
8527                      

In [75]:
dj_df_for_json=df_db_final.copy()

In [76]:
dj_df_for_json['keyParameter']=None
dj_df_for_json['compliance']=None
dj_df_for_json['probableMatchedParameter']=None
dj_df_for_json['fssrLimits']=None

In [77]:
dj_df_for_json

Quality Characteristics      Results  \
0                       Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                     Extraneous matter         0.18   
30                                    Extraneous matter         0.27   
57                                    Extraneous matter         0.20   
84    Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   
...                                                 ...          ...   
8527                                 Enterobacteriaceae          150   
8528                                        Salmonella,       Absent   
8529                        Sulfite reducing clostridia          <10   
8530                                    Bacillus Cereus          <10   
8531                                Aerobic Plate Count    2.43*10^4   

                                         Method of test        Units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30       FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57       FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84    FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   
...                                                 ...          ...   
8527                                ISO:21528(P-2):2017        cfu/g   
8528                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8529                                ISO:15123(P-1):2023        cfu/g   
8530                                  IS:5887(P-6):2012        cfu/g   
8531                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   LOQ  \
0                      Absent  None   
3           Not more than 1.0  None   
30          Not more than 1.0  None   
57          Not more than 1.0  None   
84                     Absent  None   
...                       ...   ...   
8527               Max 1X10^3  None   
8528                   Absent  None   
8529               Max 1X10^3  None   
8530               Max 1X10^4  None   
8531               Max 1X10^7  None   

                                               Order ID OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30    1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57     1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84       1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  
...                                                 ...            ...   
8527  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8528  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8529  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8530  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8531  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  ...       Parameter Name (Google Sheet)  \
0                 %   BLQ of 0.01  ...                                 NaN   
3       % by weight          0.18  ...                                 NaN   
30      % by weight          0.27  ...                                 NaN   
57      % by weight          0.20  ...                                 NaN   
84                %   BLQ of 0.01  ...                                 NaN   
...             ...           ...  ...                                 ...   
8527          cfu/g           150  ...           Enterobacteriaceae, CFU/g   
8528        Per 25g        Absent  ...                 Salmonella, Per 25g   
8529          cfu/g           <10  ...  Sulfite reducing clostridia, CFU/g   
8530          cfu/g           <10  ...              Bacillus Cereus, CFU/g   
8531          cfu/g     2.43*10^4  ...          Aerobic Plate Count, CFU/g   

     Un

DJ_df_clean according to json

In [78]:
"""
Cell generated by Data Wrangler.
"""
def clean_data(dj_df_for_json):
    # Rename column 'Quality Characteristics' to 'parameter'
    dj_df_for_json = dj_df_for_json.rename(columns={'Quality Characteristics': 'parameter'})
    # Rename column 'Results_with_units' to 'parsedValue'
    dj_df_for_json = dj_df_for_json.rename(columns={'Results_with_units': 'parsedValue'})
    # Rename column 'Method of test' to 'testMethod'
    dj_df_for_json = dj_df_for_json.rename(columns={'Method of test': 'testMethod'})
    # Rename column 'LOQ' to 'loq'
    dj_df_for_json = dj_df_for_json.rename(columns={'LOQ': 'loq'})
    # Rename column 'Order ID' to 'orderId'
    dj_df_for_json = dj_df_for_json.rename(columns={'Order ID': 'orderId'})
    # Rename column 'Units' to 'units'
    dj_df_for_json = dj_df_for_json.rename(columns={'Units': 'units'})
    return dj_df_for_json

dj_df_for_json_clean = clean_data(dj_df_for_json.copy())
dj_df_for_json_clean.head()

parameter      Results  \
0                     Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                   Extraneous matter         0.18   
30                                  Extraneous matter         0.27   
57                                  Extraneous matter         0.20   
84  Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   

                                           testMethod        units  \
0   FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3      FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30     FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57     FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84  FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   

   Prescribed Limit by FSSR   loq  \
0                    Absent  None   
3         Not more than 1.0  None   
30        Not more than 1.0  None   
57        Not more than 1.0  None   
84                   Absent  None   

                                              orderId OpinionRemarks  \
0          0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3   1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30  1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57   1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84     1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  

   Unit_extracted Results_clean  ... Parameter Name (Google Sheet) Unnamed: 2  \
0               %   BLQ of 0.01  ...                           NaN        NaN   
3     % by weight          0.18  ...                           NaN        NaN   
30    % by weight          0.27  ...                           NaN        NaN   
57    % by weight          0.20  ...                           NaN        NaN   
84              %   BLQ of 0.01  ...                           NaN        NaN   

   Parameter_Key_DB Parameter Name (Google Sheet)_seq  Required_Results  \
0     metanilYellow          Other harmful substances             0.001   
3     metanilYellow          Other harmful substances             0.180   
30    metanilYellow          Other harmful substances             0.270   
57    metanilYellow          Other harmful substances             0.200   
84    metanilYellow          Other harmful substances             0.001   

          parsedValue keyParameter  compliance probableMatchedParameter  \
0      BLQ of 0.01, %         None        None                     None   
3   0.18, % by weight         None        None                     None   
30  0.27, % by weight         None        None                     None   
57  0.20, % by weight         None        None                     None   
84     BLQ of 0.01, %         None        None                     None   

   fssrLimits  
0        None  
3        None  
30       None  
57       None  
84       None  

[5 rows x 26 columns]

In [84]:
dj_df_for_json_clean

parameter      Results  \
0                       Rodent/Animal/Mammalian excreta  BLQ of 0.01   
3                                     Extraneous matter         0.18   
30                                    Extraneous matter         0.27   
57                                    Extraneous matter         0.20   
84    Dead Insects, Insect Fragments, Rodent/Animal/...  BLQ of 0.01   
...                                                 ...          ...   
8527                                 Enterobacteriaceae          150   
8528                                        Salmonella,       Absent   
8529                        Sulfite reducing clostridia          <10   
8530                                    Bacillus Cereus          <10   
8531                                Aerobic Plate Count    2.43*10^4   

                                             testMethod        units  \
0     FSSAI Manual_Spices, Herbs and\nCondiments_No....            %   
3        FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
30       FSSAI 10.002.2021\n(Spices Herbs & Condiments)  % by weight   
57       FSSAI 10.002:2021\n(Spices Herbs & Condiments)  % by weight   
84    FSSAI Manual_Spices, Herbs and Condiments_No. ...            %   
...                                                 ...          ...   
8527                                ISO:21528(P-2):2017        cfu/g   
8528                           IS:5887(P-3)(Sec-1):2020      Per 25g   
8529                                ISO:15123(P-1):2023        cfu/g   
8530                                  IS:5887(P-6):2012        cfu/g   
8531                                  IS:5402(P-1):2021        cfu/g   

     Prescribed Limit by FSSR   loq  \
0                      Absent  None   
3           Not more than 1.0  None   
30          Not more than 1.0  None   
57          Not more than 1.0  None   
84                     Absent  None   
...                       ...   ...   
8527               Max 1X10^3  None   
8528                   Absent  None   
8529               Max 1X10^3  None   
8530               Max 1X10^4  None   
8531               Max 1X10^7  None   

                                                orderId OpinionRemarks  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295                  
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683                  
30    1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670                  
57     1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665                  
84       1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423                  
...                                                 ...            ...   
8527  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8528  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8529  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8530  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  
8531  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...                  

     Unit_extracted Results_clean  ...       Parameter Name (Google Sheet)  \
0                 %   BLQ of 0.01  ...                                 NaN   
3       % by weight          0.18  ...                                 NaN   
30      % by weight          0.27  ...                                 NaN   
57      % by weight          0.20  ...                                 NaN   
84                %   BLQ of 0.01  ...                                 NaN   
...             ...           ...  ...                                 ...   
8527          cfu/g           150  ...           Enterobacteriaceae, CFU/g   
8528        Per 25g        Absent  ...                 Salmonella, Per 25g   
8529          cfu/g           <10  ...  Sulfite reducing clostridia, CFU/g   
8530          cfu/g           <10  ...              Bacillus Cereus, CFU/g   
8531          cfu/g     2.43*10^4  ...          Aerobic Plate Count, CFU/g   

     Unnamed: 2      

In [85]:
dj_df_for_json_clean.to_excel("dj_dj.xlsx",index=False)

In [83]:
#tryinh new 
df=dj_df_for_json_clean.copy()
import json
# Group by orderId
grouped = df.groupby('orderId')
# Function to process each group
def process_group(group):
    result = {
        "orderId": group['orderId'].iloc[0],
        "matched": [],
        "mismatched": [],
        "missed": [],
        "notInScope": [],
        "sampleComplianceDetails": {
            "overallSafetyCompliant": "Safe",
            "overallLabellingCompliant": "Branded",
            "overallQualityCompliant": "Standard",
            "overallSampleClassification": "Safe"
        }
    }
    for _, row in group.iterrows():
        if row['review-suggest'] == 'matched':
            result["matched"].append({
                "parameter": row['parameter'],
                "parameterValue": row['Results'],
                "parsedValue": row['Results_clean'],
                "parameterSubCategory": row['Parameter Name (Google Sheet)'],
                "keyParameter": row['keyParameter'],
                "units": row['units'],
                "loq": row['loq'],
                "fssrLimits": row['fssrLimits'],
                "testMethod": row['testMethod'],
                "compliance": row['compliance']
            })
        else:
            result["mismatched"].append({
                "parsedParameter": row['parameter'],
                "probableMatchedParameter": row['probableMatchedParameter'],
                "parameterValue": row['Results'],
                "parsedValue": row['Results_clean'],
                "keyParameter": row['keyParameter'],
                "parameterSubCategory": row['Parameter Name (Google Sheet)'],
                "units": row['units'],
                "loq": row['loq'],
                "fssrLimits": row['fssrLimits'],
                "testMethod": row['testMethod'],
                "compliance": row['compliance']
            })
    return result
# Apply the function to each group and convert to JSON
json_result = grouped.apply(process_group).tolist()
json_output = json.dumps(json_result, indent=4)
# Assign the result back to df
df = pd.DataFrame({'Answer': [json_output]})
with open("output.json", "w", encoding="utf-8") as json_file:
    json_file.write(json_output)

print("JSON file saved successfully as output.json")

JSON file saved successfully as output.json


In [82]:
df

Answer
0  [\n    {\n        "orderId": "000311_report_FS...

In [73]:
# Assuming dj_df_for_json_clean is already defined and contains the data
# Group by orderId and apply the required transformations
def transform_group(group):
    matched = group[group['matching_score'] >= 95].to_dict(orient='records')
    mismatched = group[(group['matching_score'] < 95) & (group['matching_score'] >= 50)].to_dict(orient='records')
    missed = group[group['matching_score'] < 50]['parameter'].tolist()
    not_in_scope = group[group['matching_score'].isnull()].to_dict(orient='records')
    sample_compliance_details = {
        "overallSafetyCompliant": "Safe" if all(group['compliance'] == 'Safe') else "UnSafe",
        "overallLabellingCompliant": "Branded" if all(group['compliance'] == 'Branded') else "Unbranded",
        "overallQualityCompliant": "Standard" if all(group['compliance'] == 'Standard') else "Sub-Standard",
        "overallSampleClassification": "Safe" if all(group['compliance'] == 'Safe') else "UnSafe"
    }
    return {
        "orderId": group['orderId'].iloc[0],
        "matched": matched,
        "mismatched": mismatched,
        "missed": missed,
        "notInScope": not_in_scope,
        "sampleComplianceDetails": sample_compliance_details
    }
result = dj_df_for_json_clean.groupby('orderId').apply(transform_group).tolist()
# Convert result to DataFrame
dj_df_for_json_clean = pd.DataFrame(result, columns=['Answer'])

In [ ]:
# Fixing the code error and generating JSON format
dj_df_for_json_clean = dj_df_for_json_clean.to_dict(orient='records')
json_data = []
for record in dj_df_for_json_clean:
    json_record = {
        "orderId": record.get("orderId"),
        "matched": [
            {
                "parameter": record.get("parameter"),
                "parameterValue": record.get("Results"),
                "parsedValue": record.get("parsedValue"),
                "parameterSubCategory": record.get("parameterSubCategory"),
                "keyParameter": record.get("keyParameter"),
                "units": record.get("units"),
                "loq": record.get("loq"),
                "fssrLimits": record.get("fssrLimits"),
                "testMethod": record.get("testMethod"),
                "compliance": record.get("compliance")
            }
        ],
        "mismatched": [
            {
                "parsedParameter": record.get("parameter"),
                "probableMatchedParameter": record.get("probableMatchedParameter"),
                "parameterValue": record.get("Results"),
                "parsedValue": record.get("parsedValue"),
                "keyParameter": record.get("keyParameter"),
                "parameterSubCategory": record.get("parameterSubCategory"),
                "units": record.get("units"),
                "loq": record.get("loq"),
                "fssrLimits": record.get("fssrLimits"),
                "testMethod": record.get("testMethod"),
                "compliance": record.get("compliance")
            }
        ],
        "missed": [],
        "notInScope": [
            {
                "parameter": record.get("parameter"),
                "parameterValue": record.get("Results"),
                "parsedValue": record.get("parsedValue"),
                "parameterSubCategory": record.get("parameterSubCategory"),
                "keyParameter": record.get("keyParameter"),
                "units": record.get("units"),
                "loq": record.get("loq"),
                "fssrLimits": record.get("fssrLimits"),
                "testMethod": record.get("testMethod"),
                "compliance": record.get("compliance")
            }
        ],
        "sampleComplianceDetails": {
            "overallSafetyCompliant": "Safe",
            "overallLabellingCompliant": "Branded",
            "overallQualityCompliant": "Standard",
            "overallSampleClassification": "Safe"
        }
    }
    json_data.append(json_record)


dj_df_for_json_clean = json_data

In [63]:
dj_df_for_json_clean

[{'orderId': '0310_report_FS-KA-BE-TURMERIC_WHOLE-152295',
  'matched': [{'parameter': 'Rodent/Animal/Mammalian excreta',
    'parameterValue': 'BLQ of 0.01',
    'parsedValue': 'BLQ of 0.01, %',
    'parameterSubCategory': None,
    'keyParameter': None,
    'units': '%',
    'loq': None,
    'fssrLimits': None,
    'testMethod': 'FSSAI Manual_Spices, Herbs and\nCondiments_No. 10.002: 2021',
    'compliance': None}],
  'mismatched': [{'parsedParameter': 'Rodent/Animal/Mammalian excreta',
    'probableMatchedParameter': None,
    'parameterValue': 'BLQ of 0.01',
    'parsedValue': 'BLQ of 0.01, %',
    'keyParameter': None,
    'parameterSubCategory': None,
    'units': '%',
    'loq': None,
    'fssrLimits': None,
    'testMethod': 'FSSAI Manual_Spices, Herbs and\nCondiments_No. 10.002: 2021',
    'compliance': None}],
  'missed': [],
  'notInScope': [{'parameter': 'Rodent/Animal/Mammalian excreta',
    'parameterValue': 'BLQ of 0.01',
    'parsedValue': 'BLQ of 0.01, %',
    'paramet

In [62]:
pd.DataFrame(dj_df_for_json_clean)

orderId  \
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295   
1     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683   
2     1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670   
3      1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665   
4        1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423   
...                                                 ...   
7783  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
7784  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
7785  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
7786  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   
7787  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   

                                                matched  \
0     [{'parameter': 'Rodent/Animal/Mammalian excret...   
1     [{'parameter': 'Extraneous matter', 'parameter...   
2     [{'parameter': 'Extraneous matter', 'parameter...   
3     [{'parameter': 'Extraneous matter', 'parameter...   
4     [{'parameter': 'Dead Insects, Insect Fragments...   
...                                                 ...   
7783  [{'parameter': 'Enterobacteriaceae', 'paramete...   
7784  [{'parameter': 'Salmonella,', 'parameterValue'...   
7785  [{'parameter': 'Sulfite reducing clostridia', ...   
7786  [{'parameter': 'Bacillus Cereus', 'parameterVa...   
7787  [{'parameter': 'Aerobic Plate Count', 'paramet...   

                                             mismatched missed  \
0     [{'parsedParameter': 'Rodent/Animal/Mammalian ...     []   
1     [{'parsedParameter': 'Extraneous matter', 'pro...     []   
2     [{'parsedParameter': 'Extraneous matter', 'pro...     []   
3     [{'parsedParameter': 'Extraneous matter', 'pro...     []   
4     [{'parsedParameter': 'Dead Insects, Insect Fra...     []   
...                                                 ...    ...   
7783  [{'parsedParameter': 'Enterobacteriaceae', 'pr...     []   
7784  [{'parsedParameter': 'Salmonella,', 'probableM...     []   
7785  [{'parsedParameter': 'Sulfite reducing clostri...     []   
7786  [{'parsedParameter': 'Bacillus Cereus', 'proba...     []   
7787  [{'parsedParameter': 'Aerobic Plate Count', 'p...     []   

                                             notInScope  \
0     [{'parameter': 'Rodent/Animal/Mammalian excret...   
1     [{'parameter': 'Extraneous matter', 'parameter...   
2     [{'parameter': 'Extraneous matter', 'parameter...   
3     [{'parameter': 'Extraneous matter', 'parameter...   
4     [{'parameter': 'Dead Insects, Insect Fragments...   
...                                                 ...   
7783  [{'parameter': 'Enterobacteriaceae', 'paramete...   
7784  [{'parameter': 'Salmonella,', 'parameterValue'...   
7785  [{'parameter': 'Sulfite reducing clostridia', ...   
7786  [{'parameter': 'Bacillus Cereus', 'parameterVa...   
7787  [{'parameter': 'Aerobic Plate Count', 'paramet...   

                                sampleComplianceDetails  
0     {'overallSafetyCompliant': 'Safe', 'overallLab...  
1     {'overallSafetyCompliant': 'Safe', 'overallLab...  
2     {'overallSafetyCompliant': 'Safe', 'overallLab...  
3     {'overallSafetyCompliant': 'Safe', 'overallLab...  
4     {'overallSafetyCompliant': 'Safe', 'overallLab...  
...                                                 ...  
7783  {'overallSafetyCompliant': 'Safe', 'overallLab...  
7784  {'overallSafetyCompliant': 'Safe', 'overallLab...  
7785  {'overallSafetyCompliant': 'Safe', 'overallLab...  
7786  {'overallSafetyCompliant': 'Safe', 'overallLab...  
7787  {'overallSafetyCompliant': 'Safe', 'overallLab...  

[7788 rows x 6 columns]

#### Pivot table for Converted results

In [40]:

# Pivot the DataFrame
pivot_df = df_db_final.pivot(index='Order ID', columns='Parameter Name (Google Sheet)', values='Required_Results')

# Reset index for better readability
pivot_df.reset_index(inplace=True)
print(pivot_df.shape)

# with pd.ExcelWriter('db_mapping_turmeric_all_lab_140225.xlsx') as writer:
#     pivot_df.to_excel(writer,index=False, sheet_name='Required_results')
pivot_df.head()

(32, 299)


Parameter Name (Google Sheet)                                           Order ID  \
0                                  000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
1                                     0310_report_FS-KA-BE-TURMERIC_WHOLE-152295   
2                              1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683   
3                              1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670   
4                               1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665   

Parameter Name (Google Sheet)   NaN  \
0                              0.00   
1                               NaN   
2                               NaN   
3                              9.48   
4                               NaN   

Parameter Name (Google Sheet)  (b) Ethylene bis- dithiocarbamates resulting from the use of mancozeb, maneb or zineb (including zineb derived from nabam plus zinc\nsulphate)  \
0                                                                            NaN                                                                                                
1                                                                            NaN                                                                                                
2                                                                            NaN                                                                                                
3                                                                            NaN                                                                                                
4                                                                            NaN                                                                                                

Parameter Name (Google Sheet)  2,4-D Amine Salt  \
0                                        0.0001   
1                                        0.0008   
2                                           NaN   
3                                           NaN   
4                                           NaN   

Parameter Name (Google Sheet)  2,4-Dichlorophenoxy Acetic Acid  \
0                                                       0.0001   
1                                                       0.0008   
2                                                          NaN   
3                                                          NaN   
4                                                          NaN   

Parameter Name (Google Sheet)  Abamectin, mg/kg  \
0                                        0.0001   
1                                        0.0008   
2                                        0.0010   
3                                        0.0010   
4                                        0.0010   

Parameter Name (Google Sheet)  Acephate (expressed as mixture of Methamidophos and acephate).  \
0                                                                         0.0001                
1                                                                         0.0008                
2                                                                            NaN                
3                                                                            NaN                
4                                                                            NaN                

Parameter Name (Google Sheet)  Acetamiprid, mg/kg  Added Colouring Matter  \
0                                          0.0001                     0.0   
1                                          0.0008                     0.0   
2                                          0.0050                     NaN   
3                                          0.0050                     NaN   
4                                          0.0050                     NaN   

Parameter Name (Google Sheet)  Added Starch  ...  Trichlorfon  \
0                                       NaN  ...       0.0001   
1         

##### Required Header Sequence

In [42]:
param_to_db['Parameter Name (Google Sheet)'].dropna()
param_to_db_c = pd.DataFrame(columns= ['Order ID'] + ["commodity", "state", "district", "sampleType", "status", "sampleVariant", "lab",
    "Lab Overall Compliance", "Overall Safety Compliance", "Overall Quality Compliance",
    "Overall Label Compliance", "Opinion"] + list(param_to_db['Parameter Name (Google Sheet)'].dropna()))


pivot_df1 = pd.DataFrame()
pivot_df1 = pivot_df.reindex(columns=param_to_db_c.columns)
pivot_df = pivot_df1

#### Pivot table Results with units

In [43]:
# Pivot the DataFrame for Results with units


pivot_df_R = df_db_final.pivot(index='Order ID', columns='Parameter Name (Google Sheet)', values='Results_with_units')

# Reset index for better readability
pivot_df_R.reset_index(inplace=True)
pivot_df_R = pivot_df_R.reindex(columns=param_to_db_c.columns)
print(pivot_df_R.shape)
pivot_df_R.head()
# with pd.ExcelWriter('db_mapping_turmeric_all_lab_140225.xlsx') as writer:
    # pivot_df.to_excel(writer,index=False, sheet_name='Required_results')
# pivot_df_R.to_excel( writer,index=False, sheet_name='Results_with_units')

(32, 341)


Order ID  commodity  state  \
0      000311_report_FS-KL-PA-TURMERIC_POWDER-126904        NaN    NaN   
1         0310_report_FS-KA-BE-TURMERIC_WHOLE-152295        NaN    NaN   
2  1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683        NaN    NaN   
3  1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670        NaN    NaN   
4   1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665        NaN    NaN   

   district  sampleType  status  sampleVariant  lab  Lab Overall Compliance  \
0       NaN         NaN     NaN            NaN  NaN                     NaN   
1       NaN         NaN     NaN            NaN  NaN                     NaN   
2       NaN         NaN     NaN            NaN  NaN                     NaN   
3       NaN         NaN     NaN            NaN  NaN                     NaN   
4       NaN         NaN     NaN            NaN  NaN                     NaN   

   Overall Safety Compliance  ...          Phosphamidon             Captafol  \
0                        NaN  ...            BLQ, mg/kg           BLQ, mg/kg   
1                        NaN  ...   BLQ of 0.008, mg/kg  BLQ of 0.008, mg/kg   
2                        NaN  ...  BLQ(LOQ-0.01), mg/kg                  NaN   
3                        NaN  ...  BLQ(LOQ-0.01), mg/kg                  NaN   
4                        NaN  ...  BLQ(LOQ-0.01), mg/kg                  NaN   

                Ferbam           Formothion              Simazine  \
0                  NaN           BLQ, mg/kg            BLQ, mg/kg   
1  BLQ of 0.010, mg/kg  BLQ of 0.008, mg/kg   BLQ of 0.008, mg/kg   
2                  NaN                  NaN  BLQ(LOQ-0.01), mg/kg   
3                  NaN                  NaN  BLQ(LOQ-0.01), mg/kg   
4                  NaN                  NaN  BLQ(LOQ-0.01), mg/kg   

               Diazinon                D.D.T          Fenitrothion  \
0            BLQ, mg/kg           BLQ, mg/kg            BLQ, mg/kg   
1   BLQ of 0.008, mg/kg  BLQ of 0.008, mg/kg   BLQ of 0.008, mg/kg   
2  BLQ(LOQ-0.01), mg/kg                  NaN  BLQ(LOQ-0.01), mg/kg   
3  BLQ(LOQ-0.01), mg/kg                  NaN  BLQ(LOQ-0.01), mg/kg   
4  BLQ(LOQ-0.01), mg/kg                  NaN  BLQ(LOQ-0.01), mg/kg   

               Fenthion      Ethyl Parathion  
0            BLQ, mg/kg           BLQ, mg/kg  
1   BLQ of 0.008, mg/kg  BLQ of 0.008, mg/kg  
2  BLQ(LOQ-0.01), mg/kg                  NaN  
3  BLQ(LOQ-0.01), mg/kg                  NaN  
4  BLQ(LOQ-0.01), mg/kg                  NaN  

[5 rows x 341 columns]

In [44]:
df_db[['Order ID','OpinionRemarks']]

Order ID OpinionRemarks
0            0310_report_FS-KA-BE-TURMERIC_WHOLE-152295           None
1     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683           None
2     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683           None
3     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683           None
4     1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683           None
...                                                 ...            ...
8235  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...           None
8236  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...           None
8237  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...           None
8238  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...           None
8239  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...           None

[8240 rows x 2 columns]

In [45]:
df_db.isnull().sum()

Quality Characteristics                 0
Results                                 8
Method of test                        984
Units                                 566
Prescribed Limit by FSSR              293
Order ID                                0
OpinionRemarks                       8208
Unit_extracted                        588
Results_clean                           8
Param_with_unit                         0
Master                                 96
param_with_unit_alias                7998
master_param                         7998
matching_score                       7998
review-suggest                       7998
Parameter Name (Google Sheet)         206
Unnamed: 2                           8240
Parameter_Key_DB                      110
Parameter Name (Google Sheet)_seq     142
dtype: int64

In [46]:
df_db.shape

(8240, 19)

In [47]:
df_db[['Order ID','OpinionRemarks']].dropna(subset='OpinionRemarks').drop_duplicates(subset='Order ID')

Order ID  \
65    25088492 - Turmeric Whole_report_FS-TN-CO-TURM...   
91    DTRLSFF-101224005_report_FS-UK-DE-BLACK_PEPPER...   
242       000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
494          0310_report_FS-KA-BE-TURMERIC_WHOLE-152295   
763   1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683   
859   1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670   
955    1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665   
1051     1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423   
1326  1785583-9000-01_report_FS-TS-AD-TURMERIC_POWDE...   
1609  1807237-0028-01_report_FS-OD-CU-TURMERIC_POWDE...   
1892  1807238-0028-02_report_FS-OD-CU-TURMERIC_WHOLE...   
2175  1811469-0177-03_report_FS-JH-PU-BLACK_PEPPER_W...   
2455  1815162-0306-02_report_FS-OD-MA-TURMERIC_POWDE...   
2738           1893_report_FS-KL-TH-CHILLI_WHOLE-100264   
3007  202412CMFA-4421_report_FS-TN-KA-BLACK_PEPPER_P...   
3268   20664_0001_report_FS-RJ-AL-TURMERIC_WHOLE-012786   
3531  24122615432- BLACK PEPPER_report_FS-MH-MU-BLAC...   
4055    27516_report_FS-KA-BE-BLACK_PEPPER_WHOLE-470920   
4332    27519_report_FS-KA-CH-BLACK_PEPPER_WHOLE-157284   
4604    27521_report_FS-KA-CH-BLACK_PEPPER_WHOLE-631808   
4882       28046_report_FS-KA-BE-TURMERIC_POWDER-342822   
5151  95-020125-02_report_FS-UP-ME-TURMERIC_WHOLE-56...   
5660  DTRLSFF-101224020_report_FS-UK-DE-CHILLI_WHOLE...   
5913  DTRLSFF-261224007_report_FS-UK-HA-BLACK_PEPPER...   
6142  EKA1-25-01-02380_report_FS-KA-KO-CHILLI_WHOLE-...   
6445  ETHFSR2401145_report_FS-MH-NA-TURMERIC_POWDER-...   
6715  F24121424 - sOOzii_report_FS-DN-DA-BLACK_PEPPE...   
6957  FOOD SAFETY-50229(NEW)_report_FS-MH-AU-TURMERI...   
7210  Food-Safety-and-Standards-Authority-of-India-J...   
7472  FS0108000825 REPORT_report_FS-AR-PA-BLACK_PEPP...   
7735  FS0115004025 REPORT_report_FS-MZ-MA-BLACK_PEPP...   
7988  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   

                                         OpinionRemarks  
65    The lab has tested all the applicable General ...  
91    The sample of Black Pepper Powder(Sealed) bear...  
242   The sample sent for analysis conforms to the s...  
494   Turmeric Whole Sample is found to be With in N...  
763   Opinion: The sample Does not Conform as per Pr...  
859   The sample was in a condition fit for analysis...  
955   Opinion: The sample Does not Conform as per Pr...  
1051  Black Pepper Whole Sample is found to be With ...  
1326  The lab has tested all applicable General para...  
1609  The lab has tested all applicable General para...  
1892  The lab has tested all applicable General para...  
2175  The lab has tested all appllicable General par...  
2455  The lab has tested all applicable General para...  
2738  Chilli whole Sample does not comply with respe...  
3007  And I am of the opinion that the sample "FS-TN...  
3268  Opinion:- In the respect of the test performed...  
3531  Opinion: The sample Black Pepper Whole does no...  
4055  Black Pepper Whole Sample is found to be With ...  
4332  Black Pepper Whole Sample is found to be With ...  
4604  Black Pepper Whole Sample is found to be With ...  
4882  Turmeric Powder Sample is found to be With in ...  
5151  The tested sample does not conform to FSSR, 20...  
5660  Opinion:- The sample of CHILLI WHOLE(Sealed), ...  
5913  Opinion:- The sample of Black Pepper Whole(Loo...  
6142  The tested sample of "Chilli Whole" bearing Co...  
6445  Opinion: With reference to report no. 01/ETHFS...  
6715  The sample does not conform to the specificati...  
6957  Sample Conforms to provision of FSSAI Act, 200...  
7210  The sample conforms to the requirements given ...  
7472  The sample Does Not Conform & is "Unsafe" (as ...  
7735  The sample conforms to the specifications laid...  
7988  The sample conforms to the specifications laid...

In [48]:
df_db[['Order ID','OpinionRemarks']].dropna(subset='OpinionRemarks').drop_duplicates(subset='Order ID')

Order ID  \
65    25088492 - Turmeric Whole_report_FS-TN-CO-TURM...   
91    DTRLSFF-101224005_report_FS-UK-DE-BLACK_PEPPER...   
242       000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
494          0310_report_FS-KA-BE-TURMERIC_WHOLE-152295   
763   1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683   
859   1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670   
955    1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665   
1051     1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423   
1326  1785583-9000-01_report_FS-TS-AD-TURMERIC_POWDE...   
1609  1807237-0028-01_report_FS-OD-CU-TURMERIC_POWDE...   
1892  1807238-0028-02_report_FS-OD-CU-TURMERIC_WHOLE...   
2175  1811469-0177-03_report_FS-JH-PU-BLACK_PEPPER_W...   
2455  1815162-0306-02_report_FS-OD-MA-TURMERIC_POWDE...   
2738           1893_report_FS-KL-TH-CHILLI_WHOLE-100264   
3007  202412CMFA-4421_report_FS-TN-KA-BLACK_PEPPER_P...   
3268   20664_0001_report_FS-RJ-AL-TURMERIC_WHOLE-012786   
3531  24122615432- BLACK PEPPER_report_FS-MH-MU-BLAC...   
4055    27516_report_FS-KA-BE-BLACK_PEPPER_WHOLE-470920   
4332    27519_report_FS-KA-CH-BLACK_PEPPER_WHOLE-157284   
4604    27521_report_FS-KA-CH-BLACK_PEPPER_WHOLE-631808   
4882       28046_report_FS-KA-BE-TURMERIC_POWDER-342822   
5151  95-020125-02_report_FS-UP-ME-TURMERIC_WHOLE-56...   
5660  DTRLSFF-101224020_report_FS-UK-DE-CHILLI_WHOLE...   
5913  DTRLSFF-261224007_report_FS-UK-HA-BLACK_PEPPER...   
6142  EKA1-25-01-02380_report_FS-KA-KO-CHILLI_WHOLE-...   
6445  ETHFSR2401145_report_FS-MH-NA-TURMERIC_POWDER-...   
6715  F24121424 - sOOzii_report_FS-DN-DA-BLACK_PEPPE...   
6957  FOOD SAFETY-50229(NEW)_report_FS-MH-AU-TURMERI...   
7210  Food-Safety-and-Standards-Authority-of-India-J...   
7472  FS0108000825 REPORT_report_FS-AR-PA-BLACK_PEPP...   
7735  FS0115004025 REPORT_report_FS-MZ-MA-BLACK_PEPP...   
7988  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   

                                         OpinionRemarks  
65    The lab has tested all the applicable General ...  
91    The sample of Black Pepper Powder(Sealed) bear...  
242   The sample sent for analysis conforms to the s...  
494   Turmeric Whole Sample is found to be With in N...  
763   Opinion: The sample Does not Conform as per Pr...  
859   The sample was in a condition fit for analysis...  
955   Opinion: The sample Does not Conform as per Pr...  
1051  Black Pepper Whole Sample is found to be With ...  
1326  The lab has tested all applicable General para...  
1609  The lab has tested all applicable General para...  
1892  The lab has tested all applicable General para...  
2175  The lab has tested all appllicable General par...  
2455  The lab has tested all applicable General para...  
2738  Chilli whole Sample does not comply with respe...  
3007  And I am of the opinion that the sample "FS-TN...  
3268  Opinion:- In the respect of the test performed...  
3531  Opinion: The sample Black Pepper Whole does no...  
4055  Black Pepper Whole Sample is found to be With ...  
4332  Black Pepper Whole Sample is found to be With ...  
4604  Black Pepper Whole Sample is found to be With ...  
4882  Turmeric Powder Sample is found to be With in ...  
5151  The tested sample does not conform to FSSR, 20...  
5660  Opinion:- The sample of CHILLI WHOLE(Sealed), ...  
5913  Opinion:- The sample of Black Pepper Whole(Loo...  
6142  The tested sample of "Chilli Whole" bearing Co...  
6445  Opinion: With reference to report no. 01/ETHFS...  
6715  The sample does not conform to the specificati...  
6957  Sample Conforms to provision of FSSAI Act, 200...  
7210  The sample conforms to the requirements given ...  
7472  The sample Does Not Conform & is "Unsafe" (as ...  
7735  The sample conforms to the specifications laid...  
7988  The sample conforms to the specifications laid...

In [49]:
df_db_opinion = df_db[['Order ID','OpinionRemarks']].dropna(subset='OpinionRemarks').drop_duplicates(subset='Order ID')
# df_db_opinion.to_excel('db_mapping_turmeric_all_lab_140225.xlsx',index=False, sheet_name='OpinionRemarks')
df_db_opinion

Order ID  \
65    25088492 - Turmeric Whole_report_FS-TN-CO-TURM...   
91    DTRLSFF-101224005_report_FS-UK-DE-BLACK_PEPPER...   
242       000311_report_FS-KL-PA-TURMERIC_POWDER-126904   
494          0310_report_FS-KA-BE-TURMERIC_WHOLE-152295   
763   1243 FP2 (43)_report_FS-DL-DE-CHILLI_WHOLE-737683   
859   1273 FP2 (23)_report_FS-PB-AM-CHILLI_WHOLE-012670   
955    1291 FP2 (3)_report_FS-DL-DE-CHILLI_WHOLE-187665   
1051     1663_report_FS-KL-TH-BLACK_PEPPER_WHOLE-073423   
1326  1785583-9000-01_report_FS-TS-AD-TURMERIC_POWDE...   
1609  1807237-0028-01_report_FS-OD-CU-TURMERIC_POWDE...   
1892  1807238-0028-02_report_FS-OD-CU-TURMERIC_WHOLE...   
2175  1811469-0177-03_report_FS-JH-PU-BLACK_PEPPER_W...   
2455  1815162-0306-02_report_FS-OD-MA-TURMERIC_POWDE...   
2738           1893_report_FS-KL-TH-CHILLI_WHOLE-100264   
3007  202412CMFA-4421_report_FS-TN-KA-BLACK_PEPPER_P...   
3268   20664_0001_report_FS-RJ-AL-TURMERIC_WHOLE-012786   
3531  24122615432- BLACK PEPPER_report_FS-MH-MU-BLAC...   
4055    27516_report_FS-KA-BE-BLACK_PEPPER_WHOLE-470920   
4332    27519_report_FS-KA-CH-BLACK_PEPPER_WHOLE-157284   
4604    27521_report_FS-KA-CH-BLACK_PEPPER_WHOLE-631808   
4882       28046_report_FS-KA-BE-TURMERIC_POWDER-342822   
5151  95-020125-02_report_FS-UP-ME-TURMERIC_WHOLE-56...   
5660  DTRLSFF-101224020_report_FS-UK-DE-CHILLI_WHOLE...   
5913  DTRLSFF-261224007_report_FS-UK-HA-BLACK_PEPPER...   
6142  EKA1-25-01-02380_report_FS-KA-KO-CHILLI_WHOLE-...   
6445  ETHFSR2401145_report_FS-MH-NA-TURMERIC_POWDER-...   
6715  F24121424 - sOOzii_report_FS-DN-DA-BLACK_PEPPE...   
6957  FOOD SAFETY-50229(NEW)_report_FS-MH-AU-TURMERI...   
7210  Food-Safety-and-Standards-Authority-of-India-J...   
7472  FS0108000825 REPORT_report_FS-AR-PA-BLACK_PEPP...   
7735  FS0115004025 REPORT_report_FS-MZ-MA-BLACK_PEPP...   
7988  FS0123001325 REPORT_report_FS-DL-NO-BLACK_PEPP...   

                                         OpinionRemarks  
65    The lab has tested all the applicable General ...  
91    The sample of Black Pepper Powder(Sealed) bear...  
242   The sample sent for analysis conforms to the s...  
494   Turmeric Whole Sample is found to be With in N...  
763   Opinion: The sample Does not Conform as per Pr...  
859   The sample was in a condition fit for analysis...  
955   Opinion: The sample Does not Conform as per Pr...  
1051  Black Pepper Whole Sample is found to be With ...  
1326  The lab has tested all applicable General para...  
1609  The lab has tested all applicable General para...  
1892  The lab has tested all applicable General para...  
2175  The lab has tested all appllicable General par...  
2455  The lab has tested all applicable General para...  
2738  Chilli whole Sample does not comply with respe...  
3007  And I am of the opinion that the sample "FS-TN...  
3268  Opinion:- In the respect of the test performed...  
3531  Opinion: The sample Black Pepper Whole does no...  
4055  Black Pepper Whole Sample is found to be With ...  
4332  Black Pepper Whole Sample is found to be With ...  
4604  Black Pepper Whole Sample is found to be With ...  
4882  Turmeric Powder Sample is found to be With in ...  
5151  The tested sample does not conform to FSSR, 20...  
5660  Opinion:- The sample of CHILLI WHOLE(Sealed), ...  
5913  Opinion:- The sample of Black Pepper Whole(Loo...  
6142  The tested sample of "Chilli Whole" bearing Co...  
6445  Opinion: With reference to report no. 01/ETHFS...  
6715  The sample does not conform to the specificati...  
6957  Sample Conforms to provision of FSSAI Act, 200...  
7210  The sample conforms to the requirements given ...  
7472  The sample Does Not Conform & is "Unsafe" (as ...  
7735  The sample conforms to the specifications laid...  
7988  The sample conforms to the specifications laid...

In [50]:
with pd.ExcelWriter(f'db_mapping_Dj-{commodity}.xlsx') as writer:
    pivot_df.to_excel(writer,index=False, sheet_name='Required_results')
    pivot_df_R.to_excel( writer,index=False, sheet_name='Results_with_units')
    df_db_opinion.to_excel(writer,index=False, sheet_name='OpinionRemarks')

In [49]:

# df_final.to_excel('df_final_turmeric_pvot.xlsx',index=False)
# df_final.head()

In [50]:
# temp1.head()

In [51]:

# df1 = temp1#[['Quality Characteristics','Results','Units']]
# # print(df)


# df = unit_cleaning(df1)
# df.head()

In [52]:
# df.to_excel('unitextracted.xlsx')